### Файл для просмотра векторной базы

In [1]:
import chromadb

# Подключаемся к локальному хранилищу
client = chromadb.PersistentClient(path="./chroma_storage")

# Получаем список всех коллекций
collections = client.list_collections()

# Выводим названия коллекций и количество документов
for collection in collections:
    collection_instance = client.get_collection(name=collection.name)
    num_documents = collection_instance.count()
    print(f"{collection.name}, ------- {num_documents}")


gtr-t5-large-embedding, ------- 436
paraphrase-multilingual-mpnet-base-v2-embedding, ------- 436
distiluse-base-multilingual-cased-v1-embedding, ------- 436
multi-qa-MiniLM-L6-cos-v1-embedding, ------- 436
LaBSE-embedding, ------- 436
questions_to_QA, ------- 436
paraphrase-multilingual-MiniLM-L12-v2-embedding, ------- 436
stsb-xlm-r-multilingual-embedding, ------- 436
all-mpnet-base-v2-embedding, ------- 436
msmarco-distilbert-base-v4-embedding, ------- 436
multilingual-e5-large-embedding, ------- 436
all-MiniLM-L6-v2-embedding, ------- 436
multi-qa-mpnet-base-dot-v1-embedding, ------- 436
e5-large-v2-embedding, ------- 436


In [2]:
len(collections)

14

In [2]:
collection_name = "questions_to_QA"
collection = client.get_collection(name=collection_name)

# Получаем количество документов
num_documents = collection.count()

print(f"В коллекции '{collection_name}' содержится {num_documents} документов.")

В коллекции 'questions_to_QA' содержится 436 документов.


In [3]:
data = collection.get()

In [6]:
data

{'ids': ['2402.04453v1',
  '2406.03348v1',
  '2412.07000v2',
  '0012536v1',
  '0105522v1',
  '1205.1938v1',
  '1212.0238v1',
  '1503.03168v1',
  '2308.14478v1',
  '2502.07081v2',
  '1302.4207v1',
  '1408.3002v1',
  '1506.01055v1',
  '1507.06923v1',
  '1603.02578v1',
  '1805.00559v1',
  '2002.04991v1',
  '2302.02756v1',
  '2304.02781v1',
  '2401.06793v1',
  '2402.06452v1',
  '2411.01881v2',
  '2501.16247v1',
  '1705.03921v1',
  '1710.06798v1',
  '1711.11008v1',
  '1805.04825v1',
  '1806.01756v1',
  '1806.08874v1',
  '1807.04739v1',
  '2108.01468v1',
  '2303.02715v1',
  '2306.13586v1',
  '1307.6275v1',
  '1510.05684v2',
  '2209.15308v1',
  '2308.02870v1',
  '1704.01664v1',
  '1706.01109v2',
  '1709.03423v2',
  '1710.08952v1',
  '1902.07068v1',
  '2007.02259v1',
  '2009.08578v1',
  '2104.04120v1',
  '2305.11304v2',
  '2309.00626v1',
  '2401.17200v1',
  '2406.16106v1',
  '2409.04651v1',
  '2409.18583v1',
  '1810.11363v1',
  '1908.06951v1',
  '2002.07971v2',
  '2005.09148v1',
  '2006.04059v

In [4]:
eval(data['metadatas'][2]["questions"])["question_1"]

KeyError: 'questions'

удаление коллекции

In [2]:
# Удаляем коллекцию
client.delete_collection(name="multi-qa-mpnet-base-dot-v1-embedding")

In [39]:
CONFIG_PATH = "config/embedding/questions_gen.yaml"
# CONFIG_PATH = "config/embedding/all-MiniLM-L6-v2.yaml"
# CONFIG_PATH = "config/embedding/all-mpnet-base-v2.yaml"
# CONFIG_PATH = "config/embedding/multi-qa-mpnet-base-dot-v1.yaml"
# CONFIG_PATH = "config/embedding/paraphrase-multilingual-MiniLM-L12-v2.yaml"

In [40]:
import yaml
with open(CONFIG_PATH, "r") as file:
    config_db = yaml.safe_load(file)

CHROMA_PATH = config_db["chroma_path"]
COLLECTION_NAME = config_db["collection_name"]
MODEL_NAME = config_db["model_name"]

In [41]:
from source.chroma_manager import ChromaDBManager

In [42]:
db_manager = ChromaDBManager(CHROMA_PATH, config_db["collection_name"])
len(db_manager.collection.get()['ids'])

549

# Проверка датасета

In [43]:
import os

def count_files_in_directory(directory):
    count = 0
    for _, _, files in os.walk(directory):
        count += len(files)
    return count

directory = r"E:\ImportantFiles\Documents\University\Magic App\dataset"
print(f"Число файлов: {count_files_in_directory(directory)}")

Число файлов: 549


In [46]:
import os
import hashlib
from collections import defaultdict

def get_file_hash(file_path):
    """Вычисляет SHA-256 хеш файла."""
    hasher = hashlib.sha256()
    with open(file_path, "rb") as f:
        for chunk in iter(lambda: f.read(4096), b""):
            hasher.update(chunk)
    return hasher.hexdigest()

def find_duplicates(directory):
    """Находит дубликаты файлов в указанной директории (включая подпапки)."""
    file_hashes = defaultdict(list)

    # Рекурсивный обход папок
    for root, _, files in os.walk(directory):
        for file in files:
            file_path = os.path.join(root, file)
            file_hash = get_file_hash(file_path)
            file_hashes[file_hash].append(file_path)

    # Вывод дубликатов
    duplicates = {h: paths for h, paths in file_hashes.items() if len(paths) > 1}

    if duplicates:
        print("Найдены дубликаты:")
        for paths in duplicates.values():
            print("\n".join(paths), "\n")
    else:
        print("Дубликатов не найдено.")

# Пример использования
directory_path = r"E:\ImportantFiles\Documents\University\Magic App\dataset"
find_duplicates(directory_path)


Дубликатов не найдено.
